In [2]:
import matplotlib as plt
import os
import pandas as pd
import pefile
import pickle
import seaborn as sns
# from sklearn.ensemble import AdaBoostClassifier
# from sklearn.ensemble import BaggingClassifier
# from sklearn.ensemble import ExtraTreesClassifier
# from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler
# from sklearn.neighbors import KNeighborsClassifier
# from sklearn.tree import DecisionTreeClassifier

model_file = "model.sav"

# Creating initial feature dataframe
feature_df = pd.DataFrame()

# Creating initial byte bi-gram dataframe
byte_bi_gram_features = pd.DataFrame(columns=["SAMPLE"])

# Creating initial opcode bi-gram dataframe
opcode_bi_gram_features = pd.DataFrame(columns=["SAMPLE"])

# Creating the feature selector model
selector = SelectFromModel(RandomForestClassifier(n_estimators=1000))

learning_sample = pd.read_csv("./pe-machine-learning-dataset/samples.csv")

In [3]:
learning_sample.head()

id                               md5  \
0  233283  ad27f1a72dda61d1659810c406f37ab8   
1  233284  e07bc0b1ac52036515f1df46a7e0efad   
2  233285  8108ba444af8b7eedcb460c15a00b38f   
3  233286  87a00f767ad28811ddb3cf31cbfa2ff4   
4  233287  f601c0e160672b9cd1f2955dce182b1c   

                                       sha1  \
0  f8fd630c880257c7e74c1f87929993477453d989   
1  0b0617b468b9e2ccf0f18034e2f7819ae68007de   
2  eeb4ae807d90e9d504b8df5c28299589856d3624   
3  f9dac55eaa0ff993d057f3da9121dc8e634e7e10   
4  b814342186394eea4303139e689448c652935524   

                                              sha256  total  positives  \
0  984d732c9f32197232918f2fce0aa9cedc1011d93e32ac...     67          0   
1  984de4aadb52926eee2180e5741715c56a9b2403fef925...     67          0   
2  984ee03e9735f653256cf826f7ee5b7b8d6d9b49dfb9b8...     67          0   
3  9860c331901c99da5a5abfff17948ecf28fd97c3d93c46...     67          0   
4  98595ffa4a6319cbdae4efe7a9df84c7f5d477f93e6ee0...     68          0   

        list filetype                      submitted  user_id  length  \
0  Whitelist      exe  2018-06-24 16:18:37.547651-05        1  211456   
1  Whitelist      exe  2018-06-24 16:18:37.760216-05        1   17584   
2  Whitelist      exe  2018-06-24 16:18:37.765269-05        1   47104   
3  Whitelist      exe  2018-06-24 16:18:37.769279-05        1  242816   
4  Whitelist      exe  2018-06-24 16:18:37.773252-05        1  119240   

    entropy  
0  2.231824  
1  6.143784  
2  5.694129  
3  3.918845  
4  6.168794

In [4]:
path = "./pe-machine-learning-dataset/samples/1"
pe = pefile.PE(path)


In [ ]:
iteration_counter = 0
# Iterating through all samples in the samples subdirectory
for root, dirs, files in os.walk("./pe-machine-learning-dataset/samples/"):
    for file in files:
        try:
            # Collecting PE Header features from current sample
            print(root+file)
            pe = pefile.PE(root+file)
            features = {}
            file_id = int(os.path.splitext(file)[0])
            features["SAMPLE"] = file_id
            matching_row =  learning_sample.loc[learning_sample['id'] == file_id]
            if not matching_row.empty:
                # Get the 'list' field from the dataframe
                list_value = matching_row['list'].values[0]
                # Use list_value as needed
                features["CLASSIFICATION"] = 1 if list_value == "Blacklist" else 0
                features["FILE_HEADER.MACHINE"] = [pe.FILE_HEADER.Machine if (pe.FILE_HEADER != None) else 0]
                features["FILE_HEADER.SIZEOFOPTIONALHEADER"] = [pe.FILE_HEADER.SizeOfOptionalHeader if (pe.FILE_HEADER != None) else 0]
                features["FILE_HEADER.CHARACTERISTICS"] = [pe.FILE_HEADER.Characteristics if (pe.FILE_HEADER != None) else 0]
                features["OPTIONAL_HEADER.IMAGEBASE"] = [pe.OPTIONAL_HEADER.ImageBase if (pe.OPTIONAL_HEADER != None) else 0]
                features["OPTIONAL_HEADER.MAJOROPERATINGSYSTEM"] = [pe.OPTIONAL_HEADER.MajorOperatingSystemVersion if (pe.OPTIONAL_HEADER != None) else 0]
                features["OPTIONAL_HEADER.MAJORSUBSYSTEMVERSION"] = [pe.OPTIONAL_HEADER.MajorSubsystemVersion if (pe.OPTIONAL_HEADER != None) else 0]
                features["OPTIONAL_HEADER.DLLCHARACTERISTICS"] = [pe.OPTIONAL_HEADER.DllCharacteristics if (pe.OPTIONAL_HEADER != None) else 0]
                features["OPTIONAL_HEADER.SUBSYSTEM"] = [pe.OPTIONAL_HEADER.Subsystem if (pe.OPTIONAL_HEADER != None) else 0]
                entropies = []
                if (pe.OPTIONAL_HEADER != None):
                    for section in pe.sections:
                        entropies.append(section.get_entropy())
                else:
                    entropies.append(0)
                features["PE_SECTIONS.MAXENTROPY"] = max(entropies)
                features["PE_SECTIONS.MINENTROPY"] = min(entropies)
                features["PE_SECTIONS.MEANENTROPY"] = sum(entropies) / len(entropies)
                if (pe.OPTIONAL_HEADER != None):
                    for directory in pe.OPTIONAL_HEADER.DATA_DIRECTORY:
                        features["DATA_DIRECTORY."+str(directory.name)] = [1 if ((directory.VirtualAddress != 0) and (directory.Size != 0)) else 0]
                features["VS_VERSIONINFO.Length"] = [pe.VS_VERSIONINFO[0].Length if (pe.VS_VERSIONINFO != None) else 0]
                feature_df = feature_df.append(features, ignore_index=True)
                
        except Exception as e:
            print(e)
            
            feature_df.fillna(0)
            
            iteration_counter += 1
            if iteration_counter % 10 == 0:  # Save the DataFrame after every 10 iterations
                with open('feature_df_checkpoint.pkl', 'wb') as f:
                    pickle.dump(feature_df, f)
                print(f"Checkpoint saved at iteration {iteration_counter}")
                
        with open('feature_df_final.pkl', 'wb') as f:
            pickle.dump(feature_df, f)
     
        

./pe-machine-learning-dataset/samples/1
./pe-machine-learning-dataset/samples/10
./pe-machine-learning-dataset/samples/100


C:\Users\yukun\AppData\Local\Temp\ipykernel_39552\70303947.py:39: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)
C:\Users\yukun\AppData\Local\Temp\ipykernel_39552\70303947.py:39: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)
C:\Users\yukun\AppData\Local\Temp\ipykernel_39552\70303947.py:39: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)


./pe-machine-learning-dataset/samples/1000
'PE' object has no attribute 'VS_VERSIONINFO'
./pe-machine-learning-dataset/samples/10000
./pe-machine-learning-dataset/samples/100002


C:\Users\yukun\AppData\Local\Temp\ipykernel_39552\70303947.py:39: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)


'PE' object has no attribute 'VS_VERSIONINFO'
./pe-machine-learning-dataset/samples/100003
./pe-machine-learning-dataset/samples/100004
./pe-machine-learning-dataset/samples/10001
./pe-machine-learning-dataset/samples/100014


...

./pe-machine-learning-dataset/samples/14769
./pe-machine-learning-dataset/samples/147695


C:\Users\yukun\AppData\Local\Temp\ipykernel_39552\70303947.py:39: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)
C:\Users\yukun\AppData\Local\Temp\ipykernel_39552\70303947.py:39: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)


./pe-machine-learning-dataset/samples/1477
./pe-machine-learning-dataset/samples/14770


C:\Users\yukun\AppData\Local\Temp\ipykernel_39552\70303947.py:39: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)


./pe-machine-learning-dataset/samples/147701
'PE' object has no attribute 'VS_VERSIONINFO'
./pe-machine-learning-dataset/samples/147703
'PE' object has no attribute 'VS_VERSIONINFO'


In [1]:
features_df

NameError: name 'features_df' is not defined

In [6]:
            features["CLASSIFICATION"] = [1 if ("malicious" in root) else 0]
            features["FILE_HEADER.MACHINE"] = [pe.FILE_HEADER.Machine if (pe.FILE_HEADER != None) else 0]
            features["FILE_HEADER.SIZEOFOPTIONALHEADER"] = [pe.FILE_HEADER.SizeOfOptionalHeader if (pe.FILE_HEADER != None) else 0]
            features["FILE_HEADER.CHARACTERISTICS"] = [pe.FILE_HEADER.Characteristics if (pe.FILE_HEADER != None) else 0]
            features["OPTIONAL_HEADER.IMAGEBASE"] = [pe.OPTIONAL_HEADER.ImageBase if (pe.OPTIONAL_HEADER != None) else 0]
            features["OPTIONAL_HEADER.MAJOROPERATINGSYSTEM"] = [pe.OPTIONAL_HEADER.MajorOperatingSystemVersion if (pe.OPTIONAL_HEADER != None) else 0]
            features["OPTIONAL_HEADER.MAJORSUBSYSTEMVERSION"] = [pe.OPTIONAL_HEADER.MajorSubsystemVersion if (pe.OPTIONAL_HEADER != None) else 0]
            features["OPTIONAL_HEADER.DLLCHARACTERISTICS"] = [pe.OPTIONAL_HEADER.DllCharacteristics if (pe.OPTIONAL_HEADER != None) else 0]
            features["OPTIONAL_HEADER.SUBSYSTEM"] = [pe.OPTIONAL_HEADER.Subsystem if (pe.OPTIONAL_HEADER != None) else 0]
            
            entropies = []
            if (pe.OPTIONAL_HEADER != None):
                for section in pe.sections:
                    entropies.append(section.get_entropy())
            else:
                entropies.append(0)
            features["PE_SECTIONS.MAXENTROPY"] = max(entropies)
            features["PE_SECTIONS.MINENTROPY"] = min(entropies)
            features["PE_SECTIONS.MEANENTROPY"] = sum(entropies) / len(entropies)
            if (pe.OPTIONAL_HEADER != None):
                for directory in pe.OPTIONAL_HEADER.DATA_DIRECTORY:
                    features["DATA_DIRECTORY."+str(directory.name)] = [1 if ((directory.VirtualAddress != 0) and (directory.Size != 0)) else 0]
            features["VS_VERSIONINFO.Length"] = [pe.VS_VERSIONINFO[0].Length if (pe.VS_VERSIONINFO != None) else 0]
            feature_df = feature_df.append(features, ignore_index=True)
        except Exception as e:
            print(e)
        feature_df.fillna(0)
        
        # Collecting total byte bi-gram features in current sample
        new_bi_grams = set()
        try:
            with open(root+file, "rb") as f:
                byte_bi_gram_features = byte_bi_gram_features.append({"SAMPLE": file}, ignore_index=True)
                cur_byte = f.read(1)
                prev_byte = None
                while (cur_byte != b""):
                    if prev_byte != None:
                        bi_gram = prev_byte.hex() + " " + cur_byte.hex()
                        if not bi_gram in byte_bi_gram_features.columns:
                            new_bi_grams.add(bi_gram)
                        else:
                            byte_bi_gram_features.loc[byte_bi_gram_features["SAMPLE"]==file , [bi_gram]] = 1
                    prev_byte = cur_byte
                    cur_byte = f.read(1)
        except Exception as e:
            print(e)
        new_feature_array = []
        for index, row in byte_bi_gram_features.iterrows():
            if row["SAMPLE"] == file:
                new_feature_array.append([1 for x in new_bi_grams])
            else:
                new_feature_array.append([0 for x in new_bi_grams])
        byte_bi_gram_features = pd.concat([byte_bi_gram_features, pd.DataFrame(new_feature_array, columns=list(new_bi_grams))], axis=1)

./pe-machine-learning-dataset/samples/1


C:\Users\yukun\AppData\Local\Temp\ipykernel_39388\1486883057.py:33: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)
C:\Users\yukun\AppData\Local\Temp\ipykernel_39388\1486883057.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  byte_bi_gram_features = byte_bi_gram_features.append({"SAMPLE": file}, ignore_index=True)


./pe-machine-learning-dataset/samples/10


C:\Users\yukun\AppData\Local\Temp\ipykernel_39388\1486883057.py:33: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)
C:\Users\yukun\AppData\Local\Temp\ipykernel_39388\1486883057.py:42: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  byte_bi_gram_features = byte_bi_gram_features.append({"SAMPLE": file}, ignore_index=True)


KeyboardInterrupt: 

In [15]:
selector.fit(byte_bi_gram_features.iloc[:, 1:].to_numpy(), list(feature_df["CLASSIFICATION"]))
selected_byte_features = byte_bi_gram_features.columns[selector.get_support()]

models = [RandomForestClassifier(n_estimators=1000)]
predictions = []
for model in models:
    x_train, x_test, y_train, y_test = train_test_split(sample_df[:, 2:], sample_df[:, 1])
    model.fit(x_train, y_train)
    pickle.dump(model, open(model_file, 'wb'))

C:\Users\yukun\AppData\Local\Temp\ipykernel_43688\1365534520.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  feature_df = feature_df.append(features, ignore_index=True)
C:\Users\yukun\AppData\Local\Temp\ipykernel_43688\1365534520.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  byte_bi_gram_features = byte_bi_gram_features.append({"SAMPLE": file}, ignore_index=True)


KeyboardInterrupt: 

In [12]:


        # Collecting total opcode bi-gram features in all samples
        # new_bi_grams = set()
        # try:
        #     with open(root+file, "rb") as f: # TODO: Convert this to open file in ASM
        #         opcode_bi_gram_features = opcode_bi_gram_features.append({"SAMPLE": file}, ignore_index=True)
        #         cur_opcode = f.read(1) # TODO: Convert this to find next opcode
        #         prev_opcode = None
        #         while (cur_opcode != b""):
        #             if prev_opcode != None:
        #                 bi_gram = prev_opcode.hex() + " " + cur_opcode.hex()
        #                 if not bi_gram in opcode_bi_gram_features.columns:
        #                     new_bi_grams.add(bi_gram)
        #                 else:
        #                     opcode_bi_gram_features.loc[opcode_bi_gram_features["SAMPLE"]==file , [bi_gram]] = 1
        #             prev_opcode = cur_opcode
        #             cur_opcode = f.read(1) # TODO: Convert this to find next opcode
        # except Exception as e:
        #     print(e)
        # new_feature_array = []
        # for index, row in opcode_bi_gram_features.iterrows():
        #     if row["SAMPLE"] == file:
        #         new_feature_array.append([1 for x in new_bi_grams])
        #     else:
        #         new_feature_array.append([0 for x in new_bi_grams])
        # opcode_bi_gram_features = pd.concat([opcode_bi_gram_features, pd.DataFrame(new_feature_array, columns=new_bi_grams)], axis=1)

# Selecting top 200 byte bi-gram features
selector.fit(byte_bi_gram_features.iloc[:, 1:].to_numpy(), list(feature_df["CLASSIFICATION"])) # TODO: Debug this
selected_byte_features = byte_bi_gram_features.columns[selector.get_support()]

# Selecting top 200 opcode bi-gram features
# selector.fit(opcode_bi_gram_features.iloc[:, 1:], list(feature_df["CLASSIFICATION"])) # TODO: Copy the debugged version above
# selected_opcode_features = opcode_bi_gram_features.columns[selector.get_support()]

# Creating final dataset with full feature matrix
#sample_df = pd.concat([feature_df, byte_bi_gram_features.loc[:, selected_byte_features], opcode_bi_gram_features.loc[:, selected_opcode_features]])
sample_df = pd.concat([feature_df, byte_bi_gram_features.loc[:, selected_byte_features]])

# Training and testing each classifier with 5 folds
# models = [BaggingClassifier(KNeighborsClassifier()),
#           BaggingClassifier(DecisionTreeClassifier()),
#           BaggingClassifier(RandomForestClassifier(n_estimators=1000)),
#           BaggingClassifier(ExtraTreesClassifier(n_estimators=1000)),
#           BaggingClassifier(AdaBoostClassifier(n_estimators=1000)),
#           BaggingClassifier(GradientBoostingClassifier(n_estimators=1000)),
#           KNeighborsClassifier(),
#           DecisionTreeClassifier(),
#           RandomForestClassifier(n_estimators=1000),
#           ExtraTreesClassifier(n_estimators=1000),
#           AdaBoostClassifier(n_estimators=1000),
#           GradientBoostingClassifier(n_estimators=1000)]
models = [RandomForestClassifier(n_estimators=1000)]
predictions = []
for model in models:
    # model_predictions = []
    # for i in range(5):
    #     x_train, x_test, y_train, y_test = train_test_split(sample_df[:, 2:], sample_df[:, 1])
    #     model.fit(x_train, y_train)
    #     y_pred = model.predict(x_test)
    #     model_predictions.append(y_pred)
    #     print('Classification Report')
    #     print(classification_report(y_test, y_pred))
    #     print('Confusion Matrix')
    #     confused = confusion_matrix(y_test, y_pred)
    #     f = plt.figure(figsize=(15,15))
    #     ax = f.add_subplot()
    #     sns.heatmap(confused, annot=True, fmt='g', ax=ax)
    #     ax.set_xlabel('Predicted Labels')
    #     ax.set_ylabel('True Labels')
    #     ax.set_title('Confusion Matrix')
    #     ax.xaxis.set_ticklabels(["Malicious", "Benign"])
    #     ax.yaxis.set_ticklabels(["Malicious", "Benign"])
    #     plt.show()
    #     print('True Negative: ' + str(confused[0][0]))
    #     print('True Positive: ' + str(confused[1][1]))
    #     print('False Negative: ' + str(confused[0][1]))
    #     print('False Positive: ' + str(confused[1][0]))
    x_train, x_test, y_train, y_test = train_test_split(sample_df[:, 2:], sample_df[:, 1])
    model.fit(x_train, y_train)
    pickle.dump(model, open(model_file, 'wb'))

#loaded_model = pickle.load(open(model_file, 'rb'))
    

[WinError 2] The system cannot find the file specified: './pe-machine-learning-datasetsamples.csv'


AttributeError: 'DataFrame' object has no attribute 'filna'